<a href="https://colab.research.google.com/github/poojitha13104/AI_intern/blob/main/amazon_cnn_sentimental_analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#installing kaggle library
! pip install kaggle

In [ ]:
        from google.colab import files
        files.upload()

Saving amazon.csv to amazon (1).csv


{'amazon (1).csv': b'product_id,product_name,category,discounted_price,actual_price,discount_percentage,rating,rating_count,about_product,user_id,user_name,review_id,review_title,review_content,img_link,product_link\r\nB07JW9H4J1,"Wayona Nylon Braided USB to Lightning Fast Charging and Data Sync Cable Compatible for iPhone 13, 12,11, X, 8, 7, 6, 5, iPad Air, Pro, Mini (3 FT Pack of 1, Grey)",Computers&Accessories|Accessories&Peripherals|Cables&Accessories|Cables|USBCables,\xe2\x82\xb9399,"\xe2\x82\xb91,099",64%,4.2,"24,269","High Compatibility : Compatible With iPhone 12, 11, X/XsMax/Xr ,iPhone 8/8 Plus,iPhone 7/7 Plus,iPhone 6s/6s Plus,iPhone 6/6 Plus,iPhone 5/5s/5c/se,iPad Pro,iPad Air 1/2,iPad mini 1/2/3,iPod nano7,iPod touch and more apple devices.|Fast Charge&Data Sync : It can charge and sync simultaneously at a rapid speed, Compatible with any charging adaptor, multi-port charging station or power bank.|Durability : Durable nylon braided design with premium aluminum housing and 

In [ ]:
# configuring the path of kaggle.json file
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

cp: cannot stat 'kaggle.json': No such file or directory
chmod: cannot access '/root/.kaggle/kaggle.json': No such file or directory


In [ ]:
# extracting the compressed  dataset

from zipfile import ZipFile
dataset ='/content/amazon.csv'


importing the dependencies

In [ ]:
import numpy as np
import pandas as pd
import re
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

In [ ]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [ ]:
#printing the stopwords in english
print(stopwords.words('english'))

['a', 'about', 'above', 'after', 'again', 'against', 'ain', 'all', 'am', 'an', 'and', 'any', 'are', 'aren', "aren't", 'as', 'at', 'be', 'because', 'been', 'before', 'being', 'below', 'between', 'both', 'but', 'by', 'can', 'couldn', "couldn't", 'd', 'did', 'didn', "didn't", 'do', 'does', 'doesn', "doesn't", 'doing', 'don', "don't", 'down', 'during', 'each', 'few', 'for', 'from', 'further', 'had', 'hadn', "hadn't", 'has', 'hasn', "hasn't", 'have', 'haven', "haven't", 'having', 'he', "he'd", "he'll", 'her', 'here', 'hers', 'herself', "he's", 'him', 'himself', 'his', 'how', 'i', "i'd", 'if', "i'll", "i'm", 'in', 'into', 'is', 'isn', "isn't", 'it', "it'd", "it'll", "it's", 'its', 'itself', "i've", 'just', 'll', 'm', 'ma', 'me', 'mightn', "mightn't", 'more', 'most', 'mustn', "mustn't", 'my', 'myself', 'needn', "needn't", 'no', 'nor', 'not', 'now', 'o', 'of', 'off', 'on', 'once', 'only', 'or', 'other', 'our', 'ours', 'ourselves', 'out', 'over', 'own', 're', 's', 'same', 'shan', "shan't", 'she

DATA PROCESSING

In [ ]:
# loading the data from the csv file to pandas dataframe
twitter_data = pd.read_csv('/content/amazon.csv',encoding ='ISO-8859-1')

In [ ]:
# checking the number of rows and coloumns
twitter_data.shape

(1465, 16)

In [ ]:
# printimg the firdt five rows of the datasets
twitter_data.head()

product_id                                       product_name  \
0  B07JW9H4J1  Wayona Nylon Braided USB to Lightning Fast Cha...   
1  B098NS6PVG  Ambrane Unbreakable 60W / 3A Fast Charging 1.5...   
2  B096MSW6CT  Sounce Fast Phone Charging Cable & Data Sync U...   
3  B08HDJ86NZ  boAt Deuce USB 300 2 in 1 Type-C & Micro USB S...   
4  B08CF3B7N1  Portronics Konnect L 1.2M Fast Charging 3A 8 P...   

                                            category discounted_price  \
0  Computers&Accessories|Accessories&Peripherals|...           â¹399   
1  Computers&Accessories|Accessories&Peripherals|...           â¹199   
2  Computers&Accessories|Accessories&Peripherals|...           â¹199   
3  Computers&Accessories|Accessories&Peripherals|...           â¹329   
4  Computers&Accessories|Accessories&Peripherals|...           â¹154   

  actual_price discount_percentage rating rating_count  \
0     â¹1,099                 64%    4.2       24,269   
1       â¹349                 43%      4       43,994   
2     â¹1,899                 90%    3.9        7,928   
3       â¹699                 53%    4.2       94,363   
4       â¹399                 61%    4.2       16,905   

                                       about_product  \
0  High Compatibility : Compatible With iPhone 12...   
1  Compatible with all Type C enabled devices, be...   
2  ã Fast Charger& Data Syncã-With built-in s...   
3  The boAt Deuce USB 300 2 in 1 cable is compati...   
4  [CHARGE & SYNC FUNCTION]- This cable comes wit...   

                                             user_id  \
0  AG3D6O4STAQKAY2UVGEUV46KN35Q,AHMY5CWJMMK5BJRBB...   
1  AECPFYFQVRUWC3KGNLJIOREFP5LQ,AGYYVPDD7YG7FYNBX...   
2  AGU3BBQ2V2DDAMOAKGFAWDDQ6QHA,AESFLDV2PT363T2AQ...   
3  AEWAZDZZJLQUYVOVGBEUKSLXHQ5A,AG5HTSFRRE6NL3M5S...   
4  AE3Q6KSUK5P75D5HFYHCRAOLODSA,AFUGIFH5ZAFXRDSZH...   

                                           user_name  \
0  Manav,Adarsh gupta,Sundeep,S.Sayeed Ahmed,jasp...   
1  ArdKn,Nirbhay kumar,Sagar Viswanathan,Asp,Plac...   
2  Kunal,Himanshu,viswanath,sai niharka,saqib mal...   
3  Omkar dhale,JD,HEMALATHA,Ajwadh a.,amar singh ...   
4  rahuls6099,Swasat Borah,Ajay Wadke,Pranali,RVK...   

                                           review_id  \
0  R3HXWT0LRP0NMF,R2AJM3LFTLZHFO,R6AQJGUP6P86,R1K...   
1  RGIQEG07R9HS2,R1SMWZQ86XIN8U,R2J3Y1WL29GWDE,RY...   
2  R3J3EQQ9TZI5ZJ,R3E7WBGK7ID0KV,RWU79XKQ6I1QF,R2...   
3  R3EEUZKKK9J36I,R3HJVYCLYOY554,REDECAZ7AMPQC,R1...   
4  R1BP4L2HH9TFUP,R16PVJEXKV6QZS,R2UPDB81N66T4P,R...   

                                        review_title  \
0  Satisfied,Charging is really fast,Value for mo...   
1  A Good Braided Cable for Your Type C Device,Go...   
2  Good speed for earlier versions,Good Product,W...   
3  Good product,Good one,Nice,Really nice product...   
4  As good as original,Decent,Good one for second...   

                                      review_content  \
0  Looks durable Charging is fine tooNo complains...   
1  I ordered this cable to connect my phone to An...   
2  Not quite durable and sturdy,https://m.media-a...   
3  Good product,long wire,Charges good,Nice,I bou...   
4  Bought this instead of original apple, does th...   

                                            img_link  \
0  https://m.media-amazon.com/images/W/WEBP_40237...   
1  https://m.media-amazon.com/images/W/WEBP_40237...   
2  https://m.media-amazon.com/images/W/WEBP_40237...   
3  https://m.media-amazon.com/images/I/41V5FtEWPk...   
4  https://m.media-amazon.com/images/W/WEBP_40237...   

                                        product_link  
0  https://www.amazon.in/Wayona-Braided-WN3LG1-Sy...  
1  https://www.amazon.in/Ambrane-Unbreakable-Char...  
2  https://www.amazon.in/Sounce-iPhone-Charging-C...  
3  https://www.amazon.in/Deuce-300-Resistant-Tang...  
4  https://www.amazon.in/Portronics-Konnect-POR-1...

In [ ]:
# naming the coloumnsand reading the datasets again

coloumn_names=['product_id','product_name','category','discounted_price','actual_price','discount_percentage','rating','rating_count','about_product','user_id','user_name','review_id','review_title','review_content','img_link','product_link' ]
twitter_data = pd.read_csv('/content/amazon.csv',names=coloumn_names,encoding ='ISO-8859-1')

In [ ]:
# checking the number of rows and coloumns
twitter_data.shape

(1466, 16)

In [ ]:
# printimg the firdt five rows of the datasets
twitter_data.head()

product_id                                       product_name  \
0  product_id                                       product_name   
1  B07JW9H4J1  Wayona Nylon Braided USB to Lightning Fast Cha...   
2  B098NS6PVG  Ambrane Unbreakable 60W / 3A Fast Charging 1.5...   
3  B096MSW6CT  Sounce Fast Phone Charging Cable & Data Sync U...   
4  B08HDJ86NZ  boAt Deuce USB 300 2 in 1 Type-C & Micro USB S...   

                                            category  discounted_price  \
0                                           category  discounted_price   
1  Computers&Accessories|Accessories&Peripherals|...            â¹399   
2  Computers&Accessories|Accessories&Peripherals|...            â¹199   
3  Computers&Accessories|Accessories&Peripherals|...            â¹199   
4  Computers&Accessories|Accessories&Peripherals|...            â¹329   

   actual_price  discount_percentage  rating  rating_count  \
0  actual_price  discount_percentage  rating  rating_count   
1      â¹1,099                  64%     4.2        24,269   
2        â¹349                  43%       4        43,994   
3      â¹1,899                  90%     3.9         7,928   
4        â¹699                  53%     4.2        94,363   

                                       about_product  \
0                                      about_product   
1  High Compatibility : Compatible With iPhone 12...   
2  Compatible with all Type C enabled devices, be...   
3  ã Fast Charger& Data Syncã-With built-in s...   
4  The boAt Deuce USB 300 2 in 1 cable is compati...   

                                             user_id  \
0                                            user_id   
1  AG3D6O4STAQKAY2UVGEUV46KN35Q,AHMY5CWJMMK5BJRBB...   
2  AECPFYFQVRUWC3KGNLJIOREFP5LQ,AGYYVPDD7YG7FYNBX...   
3  AGU3BBQ2V2DDAMOAKGFAWDDQ6QHA,AESFLDV2PT363T2AQ...   
4  AEWAZDZZJLQUYVOVGBEUKSLXHQ5A,AG5HTSFRRE6NL3M5S...   

                                           user_name  \
0                                          user_name   
1  Manav,Adarsh gupta,Sundeep,S.Sayeed Ahmed,jasp...   
2  ArdKn,Nirbhay kumar,Sagar Viswanathan,Asp,Plac...   
3  Kunal,Himanshu,viswanath,sai niharka,saqib mal...   
4  Omkar dhale,JD,HEMALATHA,Ajwadh a.,amar singh ...   

                                           review_id  \
0                                          review_id   
1  R3HXWT0LRP0NMF,R2AJM3LFTLZHFO,R6AQJGUP6P86,R1K...   
2  RGIQEG07R9HS2,R1SMWZQ86XIN8U,R2J3Y1WL29GWDE,RY...   
3  R3J3EQQ9TZI5ZJ,R3E7WBGK7ID0KV,RWU79XKQ6I1QF,R2...   
4  R3EEUZKKK9J36I,R3HJVYCLYOY554,REDECAZ7AMPQC,R1...   

                                        review_title  \
0                                       review_title   
1  Satisfied,Charging is really fast,Value for mo...   
2  A Good Braided Cable for Your Type C Device,Go...   
3  Good speed for earlier versions,Good Product,W...   
4  Good product,Good one,Nice,Really nice product...   

                                      review_content  \
0                                     review_content   
1  Looks durable Charging is fine tooNo complains...   
2  I ordered this cable to connect my phone to An...   
3  Not quite durable and sturdy,https://m.media-a...   
4  Good product,long wire,Charges good,Nice,I bou...   

                                            img_link  \
0                                           img_link   
1  https://m.media-amazon.com/images/W/WEBP_40237...   
2  https://m.media-amazon.com/images/W/WEBP_40237...   
3  https://m.media-amazon.com/images/W/WEBP_40237...   
4  https://m.media-amazon.com/images/I/41V5FtEWPk...   

                                        product_link  
0                                       product_link  
1  https://www.amazon.in/Wayona-Braided-WN3LG1-Sy...  
2  https://www.amazon.in/Ambrane-Unbreakable-Char...  
3  https://www.amazon.in/Sounce-iPhone-Charging-C...  
4  https://www.amazon.in/Deuce-300-Resistant-Tang...

In [ ]:
# counting the number of missing values in the dataset
twitter_data.isnull().sum()

product_id             0
product_name           0
category               0
discounted_price       0
actual_price           0
discount_percentage    0
rating                 0
rating_count           2
about_product          0
user_id                0
user_name              0
review_id              0
review_title           0
review_content         0
img_link               0
product_link           0
dtype: int64

In [ ]:
#checking the distribution of target column
twitter_data['review_content'].value_counts()

review_content
I am not big on camera usage, personally. I was even mentally prepared for a bad camera, based on some reviews here. But I was pleasantly surprised that camera clicks good photos. They are not awesome, but they are decent photos that can even be shared.Now coming to my biggest grouse; heating issue. The phone started heating up while charging, but it was just a little and so I could have ignored it. But then it started heating up more and got me very concerned. I even ordered a replacement thinking I got a defective piece. But then, after further tests, I found that it is heating more when I download huge amounts of data, for example, when I restore data of my old phone, from back up. This is ok with me as, I don't perform huge data loads regularly, definitely not on phone. Then I tested by running tasks I usually perform such as checking office mails, attending office meeting on phone, watching a video from Amazon Prime, and so on. The phone did not heat up even a little. Personally, this is good for me.At this price range, this is a good phone. But if you are camera heavy user and expect to perform heavy downloads frequently, this phone may not for you. I am personally satisfied with this phone as it works for my type of usage. I will not go into plus points of this phone as they are covered by other reviews already. I am only attempting to clarify about how this phone can suit you (or not) in terms of camera and heating. I had many questions about these aspects before buying. Perhaps this review will help you make an informed decision to buy (or avoid). Cheers.,Display - BeautyCamera - decentPerformance - AmazingBattery - ok (in 5000mah u expect more tbh)Overall good phone...Also after 1day of use, i found some network connectivity issue in my jiosim, which I'm using right now in this phone, but I'll keep update this review after 1month of usage!,It's a decent mobile under this price but few things worried me , weight of the phone, too many procedure to change some settings, no screen casting. Apart from that it has good touch, a decent camera for day light , battery life is good.,I bought this smartphone for my mom. Samusung interface is very handful for easy use. Battery is superb, last whole day. Camera is mediocre but provide original colour pictures. All in all satisfied with this smartphone that i got in sale for 9499.,Unable to do video call within same service provider as in VOLTE within same service provider video call feature is available.,Product is fine.  Nothing Fancy but for the budget it is a good phone.,BATTERY : more than enough for normal use  Not sure in gamingCAMERA : good in this segment , can record  videos in FHD 30fpsDISPLAY : since it's a LCD display the quality is  a bit less , but goodV RAM : you can add upto 2gb of virtual ram  but have to sacrifice your storage  Space to use it  OVERALL A GOOD BUDGET PHONE,Finger print is working speedy battery backup is good camera quality is also good                                                                                                                                                                                                                                                                                                                      8
I ordered this cable to connect my phone to Android Auto of car. The cable is really strong and the connection ports are really well made. I already has a Micro USB cable from Ambrane and it's still in good shape. I connected my phone to the car using the cable and it got connected well and no issues. I also connected it to the charging port and yes it has Fast Charging support.,It quality is good at this price and the main thing is that i didn't ever thought that this cable will be so long it's good one and charging power is too good and also supports fast charging,Value for money, with extra lengthð,Good, working fine,Product quality is good,Good,very good,Bought for my daughter's old pho

convert the target code 4 to 1

In [ ]:
twitter_data.replace({'review_content':{4:1}},inplace=True)

In [ ]:
#checking the distributio the target column
twitter_data['review_content'].value_counts()

review_content
I am not big on camera usage, personally. I was even mentally prepared for a bad camera, based on some reviews here. But I was pleasantly surprised that camera clicks good photos. They are not awesome, but they are decent photos that can even be shared.Now coming to my biggest grouse; heating issue. The phone started heating up while charging, but it was just a little and so I could have ignored it. But then it started heating up more and got me very concerned. I even ordered a replacement thinking I got a defective piece. But then, after further tests, I found that it is heating more when I download huge amounts of data, for example, when I restore data of my old phone, from back up. This is ok with me as, I don't perform huge data loads regularly, definitely not on phone. Then I tested by running tasks I usually perform such as checking office mails, attending office meeting on phone, watching a video from Amazon Prime, and so on. The phone did not heat up even a little. Personally, this is good for me.At this price range, this is a good phone. But if you are camera heavy user and expect to perform heavy downloads frequently, this phone may not for you. I am personally satisfied with this phone as it works for my type of usage. I will not go into plus points of this phone as they are covered by other reviews already. I am only attempting to clarify about how this phone can suit you (or not) in terms of camera and heating. I had many questions about these aspects before buying. Perhaps this review will help you make an informed decision to buy (or avoid). Cheers.,Display - BeautyCamera - decentPerformance - AmazingBattery - ok (in 5000mah u expect more tbh)Overall good phone...Also after 1day of use, i found some network connectivity issue in my jiosim, which I'm using right now in this phone, but I'll keep update this review after 1month of usage!,It's a decent mobile under this price but few things worried me , weight of the phone, too many procedure to change some settings, no screen casting. Apart from that it has good touch, a decent camera for day light , battery life is good.,I bought this smartphone for my mom. Samusung interface is very handful for easy use. Battery is superb, last whole day. Camera is mediocre but provide original colour pictures. All in all satisfied with this smartphone that i got in sale for 9499.,Unable to do video call within same service provider as in VOLTE within same service provider video call feature is available.,Product is fine.  Nothing Fancy but for the budget it is a good phone.,BATTERY : more than enough for normal use  Not sure in gamingCAMERA : good in this segment , can record  videos in FHD 30fpsDISPLAY : since it's a LCD display the quality is  a bit less , but goodV RAM : you can add upto 2gb of virtual ram  but have to sacrifice your storage  Space to use it  OVERALL A GOOD BUDGET PHONE,Finger print is working speedy battery backup is good camera quality is also good                                                                                                                                                                                                                                                                                                                      8
I ordered this cable to connect my phone to Android Auto of car. The cable is really strong and the connection ports are really well made. I already has a Micro USB cable from Ambrane and it's still in good shape. I connected my phone to the car using the cable and it got connected well and no issues. I also connected it to the charging port and yes it has Fast Charging support.,It quality is good at this price and the main thing is that i didn't ever thought that this cable will be so long it's good one and charging power is too good and also supports fast charging,Value for money, with extra lengthð,Good, working fine,Product quality is good,Good,very good,Bought for my daughter's old pho

 STEMMING(reducing into rootwords)

stemming

In [ ]:
 port_stem = PorterStemmer()

In [ ]:
def stemming(content):

  stemmed_content = re.sub('[^a-zA-Z]',' ',content) # Added space after the sub
  stemmed_content = stemmed_content.lower()
  stemmed_content = stemmed_content.split() # Corrected the typo here
  stemmed_content = [ port_stem.stem(word)for word in stemmed_content if not word in stopwords.words('english')]
  stemmed_content = ' '.join(stemmed_content)
  return stemmed_content

In [ ]:
twitter_data['stemmed_content'] = twitter_data['review_content'].apply(stemming)

In [ ]:
 twitter_data.head()

product_id                                       product_name  \
0  product_id                                       product_name   
1  B07JW9H4J1  Wayona Nylon Braided USB to Lightning Fast Cha...   
2  B098NS6PVG  Ambrane Unbreakable 60W / 3A Fast Charging 1.5...   
3  B096MSW6CT  Sounce Fast Phone Charging Cable & Data Sync U...   
4  B08HDJ86NZ  boAt Deuce USB 300 2 in 1 Type-C & Micro USB S...   

                                            category  discounted_price  \
0                                           category  discounted_price   
1  Computers&Accessories|Accessories&Peripherals|...            â¹399   
2  Computers&Accessories|Accessories&Peripherals|...            â¹199   
3  Computers&Accessories|Accessories&Peripherals|...            â¹199   
4  Computers&Accessories|Accessories&Peripherals|...            â¹329   

   actual_price  discount_percentage  rating  rating_count  \
0  actual_price  discount_percentage  rating  rating_count   
1      â¹1,099                  64%     4.2        24,269   
2        â¹349                  43%       4        43,994   
3      â¹1,899                  90%     3.9         7,928   
4        â¹699                  53%     4.2        94,363   

                                       about_product  \
0                                      about_product   
1  High Compatibility : Compatible With iPhone 12...   
2  Compatible with all Type C enabled devices, be...   
3  ã Fast Charger& Data Syncã-With built-in s...   
4  The boAt Deuce USB 300 2 in 1 cable is compati...   

                                             user_id  \
0                                            user_id   
1  AG3D6O4STAQKAY2UVGEUV46KN35Q,AHMY5CWJMMK5BJRBB...   
2  AECPFYFQVRUWC3KGNLJIOREFP5LQ,AGYYVPDD7YG7FYNBX...   
3  AGU3BBQ2V2DDAMOAKGFAWDDQ6QHA,AESFLDV2PT363T2AQ...   
4  AEWAZDZZJLQUYVOVGBEUKSLXHQ5A,AG5HTSFRRE6NL3M5S...   

                                           user_name  \
0                                          user_name   
1  Manav,Adarsh gupta,Sundeep,S.Sayeed Ahmed,jasp...   
2  ArdKn,Nirbhay kumar,Sagar Viswanathan,Asp,Plac...   
3  Kunal,Himanshu,viswanath,sai niharka,saqib mal...   
4  Omkar dhale,JD,HEMALATHA,Ajwadh a.,amar singh ...   

                                           review_id  \
0                                          review_id   
1  R3HXWT0LRP0NMF,R2AJM3LFTLZHFO,R6AQJGUP6P86,R1K...   
2  RGIQEG07R9HS2,R1SMWZQ86XIN8U,R2J3Y1WL29GWDE,RY...   
3  R3J3EQQ9TZI5ZJ,R3E7WBGK7ID0KV,RWU79XKQ6I1QF,R2...   
4  R3EEUZKKK9J36I,R3HJVYCLYOY554,REDECAZ7AMPQC,R1...   

                                        review_title  \
0                                       review_title   
1  Satisfied,Charging is really fast,Value for mo...   
2  A Good Braided Cable for Your Type C Device,Go...   
3  Good speed for earlier versions,Good Product,W...   
4  Good product,Good one,Nice,Really nice product...   

                                      review_content  \
0                                     review_content   
1  Looks durable Charging is fine tooNo complains...   
2  I ordered this cable to connect my phone to An...   
3  Not quite durable and sturdy,https://m.media-a...   
4  Good product,long wire,Charges good,Nice,I bou...   

                                            img_link  \
0                                           img_link   
1  https://m.media-amazon.com/images/W/WEBP_40237...   
2  https://m.media-amazon.com/images/W/WEBP_40237...   
3  https://m.media-amazon.com/images/W/WEBP_40237...   
4  https://m.media-amazon.com/images/I/41V5FtEWPk...   

                                        product_link  \
0                                       product_link   
1  https://www.amazon.in/Wayona-Braided-WN3LG1-Sy...   
2  https://www.amazon.in/Ambrane-Unbreakable-Char...   
3  https://www.amazon.in/Sounce-iPhone-Charging-C...   
4  https://www.amazon.in/Deuce-300-Resistant-Tang...   

                                     stemmed_content  
0                        

In [ ]:
print(twitter_data['stemmed_content'])

0                                          review content
1       look durabl charg fine toono complain charg re...
2       order cabl connect phone android auto car cabl...
3       quit durabl sturdi http media amazon com imag ...
4       good product long wire charg good nice bought ...
                              ...                        
1461    receiv product without spanner excel product l...
1462    ok got everyth mention measur cup broken expec...
1463    plastic cool bodi u find sturdi surfac put ver...
1464    instal kitchen work fine fan speed slow could ...
1465    job perfectli issu temp control perfect u need...
Name: stemmed_content, Length: 1466, dtype: object


In [ ]:
print(twitter_data['review_content'])

0                                          review_content
1       Looks durable Charging is fine tooNo complains...
2       I ordered this cable to connect my phone to An...
3       Not quite durable and sturdy,https://m.media-a...
4       Good product,long wire,Charges good,Nice,I bou...
                              ...                        
1461    I received product without spanner,Excellent p...
1462    ok,got everything as mentioned but the measuri...
1463    plastic but cool body ,u have to find sturdy s...
1464    I have installed this in my kitchen working fi...
1465    It does it job perfectly..only issue is temp c...
Name: review_content, Length: 1466, dtype: object


In [ ]:
#seperatingthe data and label
X=twitter_data['stemmed_content'].values
Y=twitter_data['review_content'].values

In [ ]:
print(X)

['review content'
 'look durabl charg fine toono complain charg realli fast good product till satisfi qualiti good product charg speed slower origin iphon cabl good qualiti would recommend http media amazon com imag w webp imag f zghl sy jpg product work well till date issu cabl also sturdi enough ask replac compani valu money'
 'order cabl connect phone android auto car cabl realli strong connect port realli well made alreadi micro usb cabl ambran still good shape connect phone car use cabl got connect well issu also connect charg port ye fast charg support qualiti good price main thing ever thought cabl long good one charg power good also support fast charg valu money extra length good work fine product qualiti good good good bought daughter old phone brand new cabl charg alreadi repack request replac check green colour past fungu insid micro usb connector clean alcohol start work check amper charg speed got around bad came braid long cabl pretti impress price blame manufactur qualit

In [ ]:
print(Y)

['review_content'
 'Looks durable Charging is fine tooNo complains,Charging is really fast, good product.,Till now satisfied with the quality.,This is a good product . The charging speed is slower than the original iPhone cable,Good quality, would recommend,https://m.media-amazon.com/images/W/WEBP_402378-T1/images/I/81---F1ZgHL._SY88.jpg,Product had worked well till date and was having no issue.Cable is also sturdy enough...Have asked for replacement and company is doing the same...,Value for money'
 "I ordered this cable to connect my phone to Android Auto of car. The cable is really strong and the connection ports are really well made. I already has a Micro USB cable from Ambrane and it's still in good shape. I connected my phone to the car using the cable and it got connected well and no issues. I also connected it to the charging port and yes it has Fast Charging support.,It quality is good at this price and the main thing is that i didn't ever thought that this cable will be so lo

In [ ]:
X_train, X_test, Y_train, Y_test =train_test_split(X,Y, test_size=0.2,random_state=2)

In [ ]:
print(X.shape, X_train.shape,X_test.shape)

(1466,) (1172,) (294,)


In [ ]:
print(X_train)

['gener write review amazon product worth everi penni amaz product sturdi good heavi qualiti metal use yet still lightweight portabl easili carri hand full open total height reach ft even cover stage buy even survey local market confid say invest right product product avail rs pay anoth rs qualiti product better decis keep mind long term use yerar month use stand fr video shoot either indoor outdoor stand strong mani option manag stabil angl even handi often use hold like gimbl though stabil video use bc compact look go fr regret like robust durabl well assembl dislik due strong built bigger size difficult record video downsid part tripod leg come pictur along mention product detail phone holder includ purchas new one alongwith product howev one phone holder given tripod box due fals detail purchas one phone holder non return product categori kept shown picturesgood well stabler want one video shootsmust camera smartphonesthey say phone holder sent one includ order alreadi one thank so

In [ ]:
print(X_test)

['receiv look good price rang use month updat review batteri leak insid pack put new one wonder scale mean great look good accuraci lightweight skinni easi store easi clean far good durabl stainless steel construct half true promis top plate obvious metal bodi also obvious plastic would even mind littl deviat promis realiti know market messag read durabl stainless steel top plate fell apart remain plastic part machin even month use seem simpli somehow glu top glue strip glue work anymor due whatev reason remov fell apart vertic storag month use weight still work press metal plate correctli back top soon store plate separ part assembl thing everi singl use pain expect give final anoth brand chanc complet review time durabl stainless steel construct want let tri differ construct even hundr buck cheaper thing price reduc today keep month without break good deal compar one plastic product receiv good start use updat futur pro con easi use good product refer friend use month much sure accur

In [ ]:
print(X_train)

['gener write review amazon product worth everi penni amaz product sturdi good heavi qualiti metal use yet still lightweight portabl easili carri hand full open total height reach ft even cover stage buy even survey local market confid say invest right product product avail rs pay anoth rs qualiti product better decis keep mind long term use yerar month use stand fr video shoot either indoor outdoor stand strong mani option manag stabil angl even handi often use hold like gimbl though stabil video use bc compact look go fr regret like robust durabl well assembl dislik due strong built bigger size difficult record video downsid part tripod leg come pictur along mention product detail phone holder includ purchas new one alongwith product howev one phone holder given tripod box due fals detail purchas one phone holder non return product categori kept shown picturesgood well stabler want one video shootsmust camera smartphonesthey say phone holder sent one includ order alreadi one thank so

In [ ]:
print(X_test)

['receiv look good price rang use month updat review batteri leak insid pack put new one wonder scale mean great look good accuraci lightweight skinni easi store easi clean far good durabl stainless steel construct half true promis top plate obvious metal bodi also obvious plastic would even mind littl deviat promis realiti know market messag read durabl stainless steel top plate fell apart remain plastic part machin even month use seem simpli somehow glu top glue strip glue work anymor due whatev reason remov fell apart vertic storag month use weight still work press metal plate correctli back top soon store plate separ part assembl thing everi singl use pain expect give final anoth brand chanc complet review time durabl stainless steel construct want let tri differ construct even hundr buck cheaper thing price reduc today keep month without break good deal compar one plastic product receiv good start use updat futur pro con easi use good product refer friend use month much sure accur

In [ ]:
# Convert text data to numerical feature vectors
vectorizer = TfidfVectorizer()

X = twitter_data['stemmed_content'].values
Y = twitter_data['review_content'].values # Keep original review_content for now if needed for comparison

X = vectorizer.fit_transform(X)

# Split data into training and testing sets
X_train, X_test, Y_train, Y_test =train_test_split(X,Y, test_size=0.2,random_state=2)

# Train the model
model = LogisticRegression(max_iter=1000)
model.fit(X_train,Y_train)

# Evaluate the model
X_train_prediction = model.predict(X_train)
training_data_accuracy =accuracy_score(Y_train,X_train_prediction)

X_test_prediction  = model.predict(X_test)
test_data_accuracy =accuracy_score(Y_test,X_test_prediction)

print('Accuracy score on the training data :',training_data_accuracy)
print('Accuracy score on the testing data :',test_data_accuracy)

Accuracy score on the training data : 0.2235494880546075
Accuracy score on the testing data : 0.09863945578231292


In [ ]:
X_train_prediction = model.predict(X_train)
training_data_accuracy =accuracy_score(Y_train,X_train_prediction)

In [ ]:
X_test_prediction  = model.predict(X_test)
test_data_accuracy =accuracy_score(Y_test,X_test_prediction)

In [ ]:
print('Accuracy score on the training data :',training_data_accuracy)

Accuracy score on the training data : 0.2235494880546075


In [ ]:
print('Accuracy score on the testing data :',test_data_accuracy)

Accuracy score on the testing data : 0.09863945578231292


In [ ]:
import pickle

In [ ]:
filename='trained_model.sav'
pickle.dump(model,open(filename,'wb'))

In [ ]:
#loading the saved model
loading_model = pickle.load(open('/content/trained_model.sav','rb'))

In [ ]:
X_new = X_test[2]
print(Y_test[2])

prediction = loading_model.predict(X_new)
print(prediction)

if (prediction[0]== 0):
  print('The news is Negative')
else:
  print('The news is Positive')

It's light weight, good looking. Stability is moderate. I got it for 399/- I hope it the price to be less that i bought. Overall Nice experience to have this beautiful table.,It's a good product but ut has few marks on it which is not going away even after cleaning. It's okay for me. Overall It's good. Also because my laptop is 15.6" display it takes up most of the space.,Table is of light weight and hope so its sturdy. Finishing is good with cup and mobile holder, will recommend this for kids writing purpose.,Worth for money. Useful for the one who wants to sit straight without bending spinal. For  WFH  perfect.,Keeps falling even at a slight push/touch. Unsafe to keep laptop. But very GOOD product if your base/floor is plain,Brought it for 399 rs, look wise its fab, very light weight,bottle doesn't fits in slot.received damaged at corner s, connectors material is foam , due to it stability decrease. Mobile stand is not adhered. And packaging is worst no bubble paper no plastic wrappi

In [ ]:

loading_model = pickle.load(open('/content/trained_model.sav','rb'))

X_new = X_test[68]
print(Y_test[68])

prediction = loading_model.predict(X_new)
print(prediction)

if (prediction[0]== 0):
  print('The news is Negative')
else:
  print('The news is Positive')

I USE PARKER INK FOR CALLIGRAPHY AND IT IS WORKING GOOD BUT PRICE LITTLE BIT HIGH,The best thing is you can use it for any pen you want. I personally see this as a smudge proof product worth buying,Good p,Nice  pimentation,,good flow of the ink and smooth writting what else is expected I loved it just go for it,Good quality ink, just go for it. I'm using it for calligraphy it's perfect!,Very dark,Obviously better than most of the inks out there. At this price it's the best option I'd say. It's adequately dark. I'm loving the experience!,Received Black quink in bottle without plastic cover at bottle neck
["I am not big on camera usage, personally. I was even mentally prepared for a bad camera, based on some reviews here. But I was pleasantly surprised that camera clicks good photos. They are not awesome, but they are decent photos that can even be shared.Now coming to my biggest grouse; heating issue. The phone started heating up while charging, but it was just a little and so I could h